## Imports

In [25]:
from geopy.geocoders import GoogleV3
from bs4 import BeautifulSoup
import requests
import time
import pandas as pd
import numpy as np
import urllib3
import re
from textwrap import shorten
import os
import geopandas as gpd

In [26]:
### Brokerage sale data
df = pd.read_csv('chicago_broker_rankings_august_2020_with_geo_points.csv')
### Geopandas read in
chicago_neighborhoods = gpd.read_file('Boundaries - Neighborhoods.geojson')

In [27]:
chicago_neighborhoods

pri_neigh               sec_neigh     shape_area     shape_len  \
0      Grand Boulevard             BRONZEVILLE  48492503.1554  28196.837157   
1         Printers Row            PRINTERS ROW  2162137.97139   6864.247156   
2        United Center           UNITED CENTER  32520512.7053  23101.363745   
3   Sheffield & DePaul      SHEFFIELD & DEPAUL  10482592.2987  13227.049745   
4        Humboldt Park           HUMBOLDT PARK  125010425.593  46126.751351   
..                 ...                     ...            ...           ...   
93      Belmont Cragin  BELMONT CRAGIN,HERMOSA  109099407.211  43311.706886   
94              Austin                  AUSTIN  170037750.826  55473.345911   
95          Gold Coast              GOLD COAST  7165705.53467  13685.479377   
96            Boystown                BOYSTOWN  3365778.97115   9780.268985   
97         River North             RIVER NORTH  38766442.5194   31506.03781   

                                             geometry  
0   MULTIPOLYGON (((-87.60671 41.81681, -87.60670 ...  
1   MULTIPOLYGON (((-87.62761 41.87437, -87.62760 ...  
2   MULTIPOLYGON (((-87.66707 41.88885, -87.66707 ...  
3   MULTIPOLYGON (((-87.65833 41.92166, -87.65835 ...  
4   MULTIPOLYGON (((-87.74060 41.88782, -87.74060 ...  
..                                                ...  
93  MULTIPOLYGON (((-87.74143 41.91698, -87.74141 ...  
94  MULTIPOLYGON (((-87.75620 41.91547, -87.75588 ...  
95  MULTIPOLYGON (((-87.62646 41.91147, -87.62640 ...  
96  MULTIPOLYGON (((-87.64878 41.93999, -87.64927 ...  
97  MULTIPOLYGON (((-87.63145 41.90390, -87.63144 ...  

[98 rows x 5 columns]

## Correction Section

## HTML popup formatter

In [28]:
df.columns

Index(['Unnamed: 0', 'MLS#', 'Unique', 'Final Agent/Team', 'agent_type',
       'TRD Notes', 'PROPERTY TYPE', 'ADDRESS', 'CITY', 'STATE OR PROVINCE',
       'ZIP OR POSTAL CODE', 'SOLD DATE', 'PRICE', 'URL', 'full_address',
       'geo_address', 'loc', 'point', 'lat', 'lon', 'altitude'],
      dtype='object')

In [29]:
def popup_html(row):
    i = row
    address = df['full_address'].iloc[i]
    team = df['Final Agent/Team'].iloc[i]
    date_sold = df['SOLD DATE'].iloc[i]
    price = df['PRICE'].iloc[i]
    agent_type = df['agent_type'].iloc[i]
    
    html = '''<!DOCTYPE html>
    <html>
    <head>
    <h4>{}</h4>'''.format(address) + '''
    </head>
    <body>
    <strong>Team:</strong> {}'''.format(team) + '''<br> 
    <strong>Date sold:</strong> {}'''.format(date_sold) + '''<br>
    <strong>Price:</strong> {}'''.format(price) + '''<br>
    <strong>Type:</strong> {}'''.format(agent_type) + '''<br>
    </body>
    </html>
    '''
    return html


### HTML reservoir

In [30]:
#     Developer(s): <strong><em>{}'''.format(developer) + '''</strong></em><br><br>

## Map Maker

In [31]:
import folium
from folium.plugins import MarkerCluster
import branca

f = folium.Figure(width=750, height=750)
m = folium.Map(location=df[["lat", "lon"]].mean().to_list(),zoom_start=8)

title_html = '''
              <h4 align="center" style="font-size:16px"><b>{}</b></h4>
             '''.format(f'Top Chicago Broker Sales - August 2022')

for _,r in chicago_neighborhoods.iterrows():
    sim_geo = gpd.GeoSeries(r['geometry'])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'blue'})
    folium.Popup(r['pri_neigh']).add_to(geo_j)
    geo_j.add_to(m)

marker_cluster = MarkerCluster().add_to(m)

for i in range(0,len(df)):
    html = popup_html(i)
    iframe = branca.element.IFrame(html=html, width=510,height=280)
    popup = folium.Popup(folium.Html(html, script=True), max_width=510)
    folium.Marker([df['lat'].iloc[i],df['lon'].iloc[i]],
                 popup=popup).add_to(marker_cluster)

m.get_root().html.add_child(folium.Element(title_html))
m.fit_bounds(bounds=df[['lat','lon']].mean().to_list(),max_zoom=15)
# m.add_to(f)
m

In [32]:
m.save('index.html')

## Map URL snagger

Map template URL: `https://trd-digital.github.io/trd-news-interactive-maps/{map-folder-name}`

In [33]:
base_name = 'https://trd-digital.github.io/trd-news-interactive-maps/'

In [34]:
cwd = os.getcwd()

cwd = cwd.split('/')

final_name = base_name + cwd[-1]
print(final_name)

https://trd-digital.github.io/trd-news-interactive-maps/Chicago_broker_rankings_08_2022
